In [2]:
import re
import numpy as np
import pandas as pd
from pprint import pprint
 
# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
 
# Enable logging for gensim - optional
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
 
# Plotting tools
import pyLDAvis
import pyLDAvis.gensim # don't skip this
import matplotlib.pyplot as plt
%matplotlib inline
    
import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

# 토큰으로 분리된 단어들 중 명사만 추출

In [3]:
# 명사 파일 로드

data=pd.read_excel('D:\\toy\\data\\data_pos_nva.xlsx')

In [4]:
# 컬럼확인

data.columns

Index(['c_n_pos_a', 'c_n_pos_v', 'c_n_pos_n_more1', 'c_n_pos_n_more2',
       't_n_pos_a', 't_n_pos_v'],
      dtype='object')

In [5]:
# 빈도 수 2개 이하는 제거한 명사만 추출

data_n=data['c_n_pos_n_more2']

In [6]:
# 결측치 제거

data_n=data_n.dropna(axis=0)

In [7]:
# 확인

data_n

0         반도체
1          전자
2          기업
3          시장
4          사업
         ... 
46236     중재위
46237      광초
46238     사할린
46239    간접흡연
46240      필순
Name: c_n_pos_n_more2, Length: 46241, dtype: object

In [8]:
# 리스트로 변환

data_nl=data_n.tolist()

In [9]:
# 확인

data_nl

['반도체',
 '전자',
 '기업',
 '시장',
 '사업',
 '기술',
 '삼성',
 '투자',
 '산업',
 '중국',
 '수출',
 '업체',
 '실적',
 '개발',
 '증가',
 '한국',
 '생산',
 '이익',
 '영업',
 '지난해',
 '제품',
 '매출',
 '세계',
 '올해',
 '전망',
 '미국',
 '대비',
 '기록',
 '성장',
 '지난',
 '국내',
 '감소',
 '분야',
 '증권',
 '규모',
 '하락',
 '부문',
 '상승',
 '대한',
 '그룹',
 '자동차',
 '최근',
 '통해',
 '확대',
 '위해',
 '때문',
 '디스플레이',
 '관련',
 '예상',
 '글로벌',
 '회사',
 '주가',
 '장비',
 '스마트폰',
 '이번',
 '이후',
 '계획',
 '정부',
 '개선',
 '경제',
 '공장',
 '회장',
 '현재',
 '이상',
 '연구원',
 '대표',
 '발표',
 '하이닉스',
 '업종',
 '수준',
 '지원',
 '업계',
 '최대',
 '부품',
 '분석',
 '가격',
 '시스템',
 '기자',
 '공급',
 '전략',
 '수요',
 '대해',
 '경우',
 '종목',
 '바이오',
 '예정',
 '일본',
 '설명',
 '판매',
 '상황',
 '단지',
 '가장',
 '인수',
 '달러',
 '기준',
 '지수',
 '공정',
 '우리',
 '거래',
 '지속',
 '메모리',
 '지역',
 '서비스',
 '라며',
 '경쟁력',
 '모바일',
 '갤럭시',
 '목표',
 '협력',
 '영향',
 '미래',
 '평가',
 '매수',
 '사장',
 '관계자',
 '기존',
 '서울',
 '전체',
 '각각',
 '건설',
 '평택',
 '진행',
 '유지',
 '중심',
 '소재',
 '해외',
 '연구',
 '시작',
 '혁신',
 '효과',
 '센터',
 '가능성',
 '문제',
 '주요',
 '사용',
 '나노',
 '확보',
 '경기',
 '경쟁',
 '의견',

In [10]:
# 뉴스 파일 로드

data_all=pd.read_excel('D:\\toy\\data\\online_news_nosw.xlsx')

In [11]:
data_all['Index']

0        198930
1        198929
2        198928
3        198926
4        198927
          ...  
86377    112553
86378    112552
86379    112551
86380    112550
86381    112549
Name: Index, Length: 86382, dtype: int64

In [12]:
data_all.columns

Index(['Index', 'content', 'created_date', 'publisher', 'section', 'title',
       '분기', '실질GDP', 'c_pos', 't_pos', 'c_n_pos', 't_n_pos'],
      dtype='object')

In [13]:
data_all['c_n_pos'][1]

"['냈다', '우세하다', '넘어', '따르면', '아니다', '업계', '효율', '된다', '수익', '격차', '조사', '연간', '일부', '개선', '머물러', '되면', '큼지막한', '센서', '생산', '부진', '위용', '전자공학', '극심한', '고속도로', '아니라', '연구개발', '사업', '예상', '증권', '수주', '처음', '악화', '축구장', '빠졌던', '빠졌다', '외부', '예정', '구매', '이를', '확대', '불과하다', '없어', '준다', '착공', '내다봤다', '양산', '당분간', '왔다', '나온다', '맡겼던', '사상', '체인지', '조용히', '브랜드', '전문', '설계', '전반', '점유', '나올', '해도', '있는', '성장할', '애플', '엑시노스', '수정', '실적', '전자기기', '전기', '차례', '수십', '잡았던', '유일하게', '하는', '사례', '상징', '수출', '핀펫', '자체', '추격', '메모리', '하락', '보이', '퀄컴', '하게', '인쇄공', '앞선', '분야', '최대', '거두는', '치를', '않다', '넘을', '차원', '대비', '솟아', '건설', '라면', '주력', '환하다', '회사', '대표', '독식', '보인다', '가장', '물량', '였다고', '높인', '크기', '역량', '가고', '가격', '하지', '모바일', '이뤄져', '격화', '크레인', '압도', '기술', '해외', '개발', '넘는', '나노미터', '시스템', '되찾아', '끊임없는', '밀려', '규모', '한층', '투자', '수준', '나선', '육박', '조짐', '이어', '느냐가', '신규', '높아질', '시장', '탑재', '국내외', '영업', '대박', '효자', '기업', '반도체', '증설', '가까이', '좁혀', '주자', '명운', '어려울', '달러', '세계', '유회', '직전', '늘어난', '계속'

In [14]:
# n_pos_t 리스트안의 문자형 분리 & 특수문자 제거

data_sp=[]
for i in range(len(data_all)):
    data_sp.append(data_all['c_n_pos'][i].split(','))
    
data_sp[0]

["['부문'",
 " '뉴스'",
 " '따르면'",
 " '떨어질'",
 " '된다'",
 " '연간'",
 " '종합'",
 " '되면'",
 " '기조'",
 " '종목'",
 " '넘길'",
 " '단가'",
 " '증권'",
 " '넘긴'",
 " '올리며'",
 " '확대'",
 " '앞서'",
 " '체인지'",
 " '대한'",
 " '있는'",
 " '성장할'",
 " '맞을'",
 " '하는'",
 " '크게'",
 " '전체'",
 " '있기'",
 " '지를'",
 " '최대'",
 " '같은'",
 " '재다'",
 " '대비'",
 " '때문'",
 " '판매'",
 " '보다'",
 " '이유'",
 " '겪은'",
 " '맛있는'",
 " '보인다'",
 " '기를'",
 " '나왔다'",
 " '서다'",
 " '성장'",
 " '모바일'",
 " '쳐지고'",
 " '이었던'",
 " '투자'",
 " '보이는데도'",
 " '포인트'",
 " '이어'",
 " '시장'",
 " '영업'",
 " '기업'",
 " '반도체'",
 " '걸까'",
 " '세계'",
 " '전자상거래'",
 " '조정'",
 " '했다'",
 " '쳐졌다'",
 " '상향'",
 " '예측'",
 " '전망'",
 " '차지'",
 " '바뀌는'",
 " '정보'",
 " '신선한'",
 " '국내'",
 " '성장한'",
 " '치가'",
 " '수요'",
 " '매출'",
 " '새해'",
 " '분석'",
 " '이익'",
 " '호황'",
 " '사이트'",
 " '역성'",
 " '됐다'",
 " '훌쩍'",
 " '갔다'",
 " '비중'",
 " '신문']"]

In [15]:
data_st=[]
for i in range(len(data_sp)):
    data_st2=[]
    for j in data_sp[i]:
        data_st2.append(j.lstrip('[').rstrip('"]').strip(" ' "))
    data_st.append(data_st2)

data_st[0][1]

'뉴스'

In [16]:
# data_nl을 세트로 변환

a=set(data_nl)

In [17]:
# 명사파일로 필터링하여 n_pos_c 컬럼의 명사만 추출

SW_del=[]
for i in data_st:
    b=set(i)
    SW_del.append(b&a)

In [18]:
# 확인

SW_del

[{'국내',
  '기업',
  '기조',
  '뉴스',
  '단가',
  '대비',
  '대한',
  '때문',
  '매출',
  '모바일',
  '반도체',
  '부문',
  '분석',
  '비중',
  '사이트',
  '상향',
  '새해',
  '성장',
  '세계',
  '수요',
  '시장',
  '신문',
  '앞서',
  '역성',
  '연간',
  '영업',
  '예측',
  '이유',
  '이익',
  '전망',
  '전자상거래',
  '전체',
  '정보',
  '조정',
  '종목',
  '종합',
  '증권',
  '차지',
  '체인지',
  '최대',
  '치가',
  '크게',
  '투자',
  '판매',
  '포인트',
  '호황',
  '확대',
  '훌쩍'},
 {'가격',
  '가까이',
  '가장',
  '개발',
  '개선',
  '거래',
  '건설',
  '격차',
  '격화',
  '경기',
  '경쟁',
  '계속',
  '계획',
  '고속도로',
  '공략',
  '공장',
  '공정',
  '과언',
  '과학기술원',
  '관계자',
  '구매',
  '국내외',
  '규모',
  '기술',
  '기업',
  '나노미터',
  '나선',
  '노릇',
  '달러',
  '당분간',
  '대박',
  '대비',
  '대표',
  '덕분',
  '독식',
  '라면',
  '로고',
  '메모리',
  '명운',
  '모바일',
  '물량',
  '미세',
  '반도체',
  '보고',
  '보이',
  '본격',
  '부진',
  '부착',
  '분석',
  '분야',
  '브랜드',
  '비메',
  '사례',
  '사상',
  '사업',
  '사이트',
  '산업',
  '상징',
  '상향',
  '새해',
  '생산',
  '선두',
  '설계',
  '설비',
  '세계',
  '센서',
  '수십',
  '수익',
  '수정',
  '수주',
  '수준',
  '수출',
  '스마트폰',
  '시스

In [19]:
# set을 리스트로 변환

SW_del2=[]
for i in SW_del:
    SW_del2.append(list(i))

In [20]:
SW_del2[55000]

['부가',
 '전장',
 '불구',
 '여력',
 '의미',
 '증가',
 '고객',
 '전세계',
 '하이엔드',
 '평가',
 '계속',
 '로서',
 '바탕',
 '글로벌',
 '지속',
 '기업',
 '선정',
 '기대',
 '의견',
 '최초',
 '포인트',
 '위해',
 '경쟁',
 '차지',
 '현금',
 '수요',
 '여개',
 '경영',
 '시장점유율',
 '제품',
 '베스트',
 '기능',
 '동사',
 '금융투자',
 '뇌수술',
 '자본',
 '공정',
 '출하',
 '주가',
 '강소기업',
 '초도',
 '실적',
 '이익',
 '검사',
 '예상',
 '추진',
 '확대',
 '머니투데이',
 '달러',
 '전망',
 '상승',
 '대해',
 '안정',
 '연간',
 '독보',
 '증권',
 '판매',
 '제시',
 '개시',
 '광학',
 '매출',
 '보고서',
 '개발',
 '차입',
 '압도',
 '가시',
 '반도체',
 '기준',
 '주력',
 '상태',
 '성과',
 '단가',
 '반영',
 '자동',
 '리포트',
 '통해',
 '목표',
 '경우',
 '커버',
 '매수',
 '내용',
 '규모',
 '사업',
 '납품',
 '영업',
 '영향',
 '신뢰',
 '장비',
 '감소',
 '투자',
 '요약',
 '대비',
 '겸비',
 '고가',
 '성장',
 '측면',
 '기술',
 '추가',
 '내비게이션',
 '고영은',
 '중이',
 '자동차',
 '시장',
 '의료',
 '물량',
 '불량품',
 '세계']

# LDA Modeling

In [21]:
# 사전 생성

id2word = corpora.Dictionary(SW_del2)

In [22]:
# 말뭉치 생성

texts = SW_del2

In [23]:
# Term Document Frequency

corpus = [id2word.doc2bow(text) for text in texts]

In [24]:
# 확인
print(corpus[0])

[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1)]


In [25]:
# 빈도수 표시

[[(id2word[id], freq) for id, freq in cp] for cp in corpus]

[[('국내', 1),
  ('기업', 1),
  ('기조', 1),
  ('뉴스', 1),
  ('단가', 1),
  ('대비', 1),
  ('대한', 1),
  ('때문', 1),
  ('매출', 1),
  ('모바일', 1),
  ('반도체', 1),
  ('부문', 1),
  ('분석', 1),
  ('비중', 1),
  ('사이트', 1),
  ('상향', 1),
  ('새해', 1),
  ('성장', 1),
  ('세계', 1),
  ('수요', 1),
  ('시장', 1),
  ('신문', 1),
  ('앞서', 1),
  ('역성', 1),
  ('연간', 1),
  ('영업', 1),
  ('예측', 1),
  ('이유', 1),
  ('이익', 1),
  ('전망', 1),
  ('전자상거래', 1),
  ('전체', 1),
  ('정보', 1),
  ('조정', 1),
  ('종목', 1),
  ('종합', 1),
  ('증권', 1),
  ('차지', 1),
  ('체인지', 1),
  ('최대', 1),
  ('치가', 1),
  ('크게', 1),
  ('투자', 1),
  ('판매', 1),
  ('포인트', 1),
  ('호황', 1),
  ('확대', 1),
  ('훌쩍', 1)],
 [('기업', 1),
  ('대비', 1),
  ('모바일', 1),
  ('반도체', 1),
  ('분석', 1),
  ('사이트', 1),
  ('상향', 1),
  ('새해', 1),
  ('세계', 1),
  ('시장', 1),
  ('연간', 1),
  ('영업', 1),
  ('예측', 1),
  ('이익', 1),
  ('전망', 1),
  ('증권', 1),
  ('차지', 1),
  ('체인지', 1),
  ('최대', 1),
  ('투자', 1),
  ('호황', 1),
  ('확대', 1),
  ('가격', 1),
  ('가까이', 1),
  ('가장', 1),
  ('개발', 1),
  ('개선', 1),
  ('거래', 1)

In [26]:
# LDA 모델 생성

lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                            id2word=id2word,
                                            num_topics=20,
                                            random_state=100,
                                            update_every=1,
                                            chunksize=100,
                                            passes=10,
                                            alpha='auto',
                                            per_word_topics=True)

In [27]:
# 토픽 출력

pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(0,
  '0.030*"지수" + 0.026*"업종" + 0.025*"거래" + 0.025*"오른" + 0.024*"상승" + 0.022*"하락" '
  '+ 0.019*"강세" + 0.019*"포인트" + 0.018*"마감" + 0.018*"증시"'),
 (1,
  '0.036*"서비스" + 0.034*"사물인터넷" + 0.034*"지능" + 0.030*"통신" + 0.030*"스마트" + '
  '0.024*"시스템" + 0.024*"제공" + 0.023*"기기" + 0.023*"플랫폼" + 0.023*"자동차"'),
 (2,
  '0.030*"우려" + 0.026*"노트" + 0.022*"가능성" + 0.019*"불확실" + 0.018*"상황" + '
  '0.017*"정책" + 0.016*"금리" + 0.015*"부담" + 0.015*"경기" + 0.014*"주의"'),
 (3,
  '0.129*"계약" + 0.113*"체결" + 0.079*"장비" + 0.069*"공급" + 0.066*"제조" + 0.060*"규모" '
  '+ 0.060*"재료" + 0.057*"반도체" + 0.045*"매출" + 0.040*"변경"'),
 (4,
  '0.019*"산업" + 0.018*"기술" + 0.018*"위해" + 0.017*"기업" + 0.017*"분야" + '
  '0.015*"반도체" + 0.015*"지원" + 0.015*"미래" + 0.014*"통해" + 0.014*"사업"'),
 (5,
  '0.098*"프로그램" + 0.089*"과학" + 0.087*"표준" + 0.084*"신뢰" + 0.057*"기여" + '
  '0.056*"합동" + 0.053*"근거" + 0.048*"과학기술" + 0.046*"규명" + 0.041*"미래창조과학부"'),
 (6,
  '0.127*"일자리" + 0.101*"특수" + 0.081*"정기" + 0.052*"개혁" + 0.050*"필요성" + '
  '0.049*"최대한" + 0.042*"행위" + 0.042*"

# 시각화

In [28]:
# Visualize the topics

pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
vis

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
8     -0.203242  0.056309       1        1  16.428934
4     -0.201685 -0.131365       2        1  13.052881
14    -0.194550  0.012997       3        1  12.172667
9     -0.109144 -0.183378       4        1   9.954166
13    -0.135658 -0.096700       5        1   9.131909
16    -0.143067 -0.186345       6        1   7.827603
12    -0.119057 -0.022218       7        1   7.101106
2     -0.046115  0.018749       8        1   4.277180
0     -0.080772  0.185106       9        1   4.156122
1      0.026626 -0.085575      10        1   3.603925
15    -0.116174  0.258037      11        1   2.490459
7     -0.010298  0.199085      12        1   2.071251
11     0.126767 -0.053320      13        1   1.915372
18     0.126660 -0.091229      14        1   1.248051
19     0.070586  0.176012      15        1   1.073600
17     0.185239 -0.145116      16        1   1.031222
3      0.053098  0.073413      17        1   0.962122
5      0.255998 -0.001813      18        1   0.607460
6      0.253344  0.004465      19        1   0.533953
10     0.261445  0.012886      20        1   0.360011, topic_info=       Term           Freq          Total Category  logprob  loglift
10      반도체  106012.000000  106012.000000  Default  30.0000  30.0000
70       규모   32698.000000   32698.000000  Default  29.0000  29.0000
886      공급   22757.000000   22757.000000  Default  28.0000  28.0000
100      생산   34295.000000   34295.000000  Default  27.0000  27.0000
388      장비   20897.000000   20897.000000  Default  26.0000  26.0000
...     ...            ...            ...      ...      ...      ...
2325   일어나지     160.518005     161.710953  Topic20  -5.2085   5.6194
657      백만     159.754044     160.946991  Topic20  -5.2133   5.6194
2411  프리스케일     137.582870     138.775818  Topic20  -5.3627   5.6182
1300    보편화     134.626785     135.819733  Topic20  -5.3844   5.6180
1799     최단     121.635414     122.828354  Topic20  -5.4859   5.6170

[1051 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
48        1  0.643390    가격
48        3  0.301163    가격
48        5  0.022324    가격
48        9  0.033080    가격
2396     12  0.999249  가계부채
...     ...       ...   ...
178       2  0.127430    효율
178       6  0.872443    효율
181       3  0.997963    후발
2533      7  0.999705    후보
608      18  0.999539    후속

[1801 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[9, 5, 15, 10, 14, 17, 13, 3, 1, 2, 16, 8, 12, 19, 20, 18, 4, 6, 7, 11])

# 키워드 추출

In [29]:
topics = lda_model.print_topics(num_words=20) #topic 별 20개 keyword 보여줌 # 이 중 가중치가 0인것들 빼고 저장시킨다. 
for topic in topics:
    print(topic)

(0, '0.030*"지수" + 0.026*"업종" + 0.025*"거래" + 0.025*"오른" + 0.024*"상승" + 0.022*"하락" + 0.019*"강세" + 0.019*"포인트" + 0.018*"마감" + 0.018*"증시" + 0.018*"코스피" + 0.017*"코스닥" + 0.017*"종목" + 0.016*"시가총액" + 0.016*"유가" + 0.016*"매수" + 0.016*"기관" + 0.015*"기록" + 0.014*"상승세" + 0.014*"전날"')
(1, '0.036*"서비스" + 0.034*"사물인터넷" + 0.034*"지능" + 0.030*"통신" + 0.030*"스마트" + 0.024*"시스템" + 0.024*"제공" + 0.023*"기기" + 0.023*"플랫폼" + 0.023*"자동차" + 0.021*"방침" + 0.020*"차량" + 0.020*"정보" + 0.018*"빅데이터" + 0.017*"데이터" + 0.015*"전문" + 0.014*"기능" + 0.014*"인터넷" + 0.014*"네트워크" + 0.013*"센서"')
(2, '0.030*"우려" + 0.026*"노트" + 0.022*"가능성" + 0.019*"불확실" + 0.018*"상황" + 0.017*"정책" + 0.016*"금리" + 0.015*"부담" + 0.015*"경기" + 0.014*"주의" + 0.013*"기업" + 0.013*"부정" + 0.012*"기조" + 0.012*"침체" + 0.012*"요인" + 0.012*"미국" + 0.012*"작용" + 0.011*"리스크" + 0.011*"정치" + 0.011*"위축"')
(3, '0.129*"계약" + 0.113*"체결" + 0.079*"장비" + 0.069*"공급" + 0.066*"제조" + 0.060*"규모" + 0.060*"재료" + 0.057*"반도체" + 0.045*"매출" + 0.040*"변경" + 0.038*"기간" + 0.033*"사항" + 0.018*"답변" + 0.016*"

In [30]:
topics[0][1]

'0.030*"지수" + 0.026*"업종" + 0.025*"거래" + 0.025*"오른" + 0.024*"상승" + 0.022*"하락" + 0.019*"강세" + 0.019*"포인트" + 0.018*"마감" + 0.018*"증시" + 0.018*"코스피" + 0.017*"코스닥" + 0.017*"종목" + 0.016*"시가총액" + 0.016*"유가" + 0.016*"매수" + 0.016*"기관" + 0.015*"기록" + 0.014*"상승세" + 0.014*"전날"'

In [31]:
topic_0_1=topics[0][1].split('+')

In [32]:
topic_0_1

['0.030*"지수" ',
 ' 0.026*"업종" ',
 ' 0.025*"거래" ',
 ' 0.025*"오른" ',
 ' 0.024*"상승" ',
 ' 0.022*"하락" ',
 ' 0.019*"강세" ',
 ' 0.019*"포인트" ',
 ' 0.018*"마감" ',
 ' 0.018*"증시" ',
 ' 0.018*"코스피" ',
 ' 0.017*"코스닥" ',
 ' 0.017*"종목" ',
 ' 0.016*"시가총액" ',
 ' 0.016*"유가" ',
 ' 0.016*"매수" ',
 ' 0.016*"기관" ',
 ' 0.015*"기록" ',
 ' 0.014*"상승세" ',
 ' 0.014*"전날"']

In [33]:
float(topic_0_1[0].replace('*',' ').replace("\"","").split()[0])

0.03

In [34]:
topic_0_1[0].replace('*',' ').replace("\"","").split()

['0.030', '지수']

In [35]:
def make_keyword(data): #topic[0][1],topic[1],[1], . . . , topic[19][1] 이런식으로 넣음 
    topic_sep1=data.split('+')
    
    topic_keyword=[]
    topic_keyword_del=[]
    
    for i in range(20):
        topic_sep1[i]=topic_sep1[i].replace('*',' ').replace("\"","").split()
        #print(topic_sep1[i])
        
        if float(topic_sep1[i][0])>0: #가중치가 0보다 크면 keyword 에 저장 
            topic_keyword.append(topic_sep1[i][1]) 
            
        else:
            topic_keyword_del.append(topic_sep1[i][1]) #혹시 del된 단어들 보고싶다면 여기서 
            
        
    return topic_keyword

In [36]:
make_keyword(topics[0][1])

['지수',
 '업종',
 '거래',
 '오른',
 '상승',
 '하락',
 '강세',
 '포인트',
 '마감',
 '증시',
 '코스피',
 '코스닥',
 '종목',
 '시가총액',
 '유가',
 '매수',
 '기관',
 '기록',
 '상승세',
 '전날']

In [37]:
topic_keyword_all=[]

for i in range(20):
    topic_keyword_all.append(make_keyword(topics[i][1]))

topic_keyword_all   

[['지수',
  '업종',
  '거래',
  '오른',
  '상승',
  '하락',
  '강세',
  '포인트',
  '마감',
  '증시',
  '코스피',
  '코스닥',
  '종목',
  '시가총액',
  '유가',
  '매수',
  '기관',
  '기록',
  '상승세',
  '전날'],
 ['서비스',
  '사물인터넷',
  '지능',
  '통신',
  '스마트',
  '시스템',
  '제공',
  '기기',
  '플랫폼',
  '자동차',
  '방침',
  '차량',
  '정보',
  '빅데이터',
  '데이터',
  '전문',
  '기능',
  '인터넷',
  '네트워크',
  '센서'],
 ['우려',
  '노트',
  '가능성',
  '불확실',
  '상황',
  '정책',
  '금리',
  '부담',
  '경기',
  '주의',
  '기업',
  '부정',
  '기조',
  '침체',
  '요인',
  '미국',
  '작용',
  '리스크',
  '정치',
  '위축'],
 ['계약',
  '체결',
  '장비',
  '공급',
  '제조',
  '규모',
  '재료',
  '반도체',
  '매출',
  '변경',
  '기간',
  '사항',
  '답변',
  '대비',
  '전방',
  '공정',
  '수주',
  '테크',
  '국제무역',
  '중국'],
 ['산업',
  '기술',
  '위해',
  '기업',
  '분야',
  '반도체',
  '지원',
  '미래',
  '통해',
  '사업',
  '계획',
  '추진',
  '협력',
  '개발',
  '정부',
  '성과',
  '혁신',
  '구축',
  '적극',
  '전략'],
 ['프로그램',
  '과학',
  '표준',
  '신뢰',
  '기여',
  '합동',
  '근거',
  '과학기술',
  '규명',
  '미래창조과학부',
  '후속',
  '발굴',
  '수집',
  '계산',
  '제정',
  '항공우주',
  '포괄',
  '구단',
  '명목',
  '유연

In [38]:
#topic 0번 
topic_keyword_all[0]  

['지수',
 '업종',
 '거래',
 '오른',
 '상승',
 '하락',
 '강세',
 '포인트',
 '마감',
 '증시',
 '코스피',
 '코스닥',
 '종목',
 '시가총액',
 '유가',
 '매수',
 '기관',
 '기록',
 '상승세',
 '전날']

In [39]:
result=pd.DataFrame(topic_keyword_all)

In [40]:
result2=result.T

In [41]:
result

0      1    2    3     4      5      6     7    8        9     10  \
0     지수     업종   거래   오른    상승     하락     강세   포인트   마감       증시    코스피   
1    서비스  사물인터넷   지능   통신   스마트    시스템     제공    기기  플랫폼      자동차     방침   
2     우려     노트  가능성  불확실    상황     정책     금리    부담   경기       주의     기업   
3     계약     체결   장비   공급    제조     규모     재료   반도체   매출       변경     기간   
4     산업     기술   위해   기업    분야    반도체     지원    미래   통해       사업     계획   
5   프로그램     과학   표준   신뢰    기여     합동     근거  과학기술   규명  미래창조과학부     후속   
6    일자리     특수   정기   개혁   필요성    최대한     행위    권리   제재       시사     포럼   
7     수출     정부   업종   조선    경제   구조조정    자동차    규제   소비       국산     정책   
8     전망     실적   투자   증가    예상    반도체     대비    개선   이익       분석     영업   
9     문제     때문   대해   지금   대통령     이유     대한    당시   과정       지난     생각   
10    대체     단일   광학   광장  저장장치  전기자동차  하드디스크    지휘   주역      수상자     결실   
11    현지     퀄컴   미국   행사    발굴     협회     구글   소비자   나선       시대  최고경영자   
12   반도체     기업   투자   회사    결정     인수     설립   외국인   관련       화학     자금   
13    지역     산업   시설   건설    예정     공장     규모   반도체  경기도       위치     여러   
14    시장     제품   업계   생산   반도체   스마트폰     중국    최대   사업       세계     경쟁   
15    수출     감소   수입   철강    증가     무역     통상    중국   선박       별로     산업   
16    사용     개발   기술   기존    적용    반도체     활용    장치   이용      차세대     최초   
17    사장     총괄   경영   합병   텔레콤     회장    시너지   리더십   부문    최고경영자     조직   
18    건강     사고   피해   이해   노동자     보건     발생    안전   사망       거부     인용   
19   제조업     공식   동향   공업    소비     통계     설비    생산   차질       파업   서비스업   

      11   12    13   14    15      16   17     18   19  
0    코스닥   종목  시가총액   유가    매수      기관   기록    상승세   전날  
1     차량   정보  빅데이터  데이터    전문      기능  인터넷   네트워크   센서  
2     부정   기조    침체   요인    미국      작용  리스크     정치   위축  
3     사항   답변    대비   전방    공정      수주   테크   국제무역   중국  
4     추진   협력    개발   정부    성과      혁신   구축     적극   전략  
5     발굴   수집    계산   제정  항공우주      포괄   구단     명목  유연성  
6    정치권   가스   돌파구   거치    처벌      차관   장면     통제  원동력  
7     의존   재정   선진국   항공    불황    우리나라   해양     수입   중국  
8     증권   상승    지속   기록    유지      기준   가격     라며   평균  
9     현실   가장    의미   상황    처음      시대   요구     가지   지적  
10    복원  자외선  인사이트   재배    내일      본질   고수     상존   주석  
11    세계   개국    관심   참가  전자기기  라스베이거스   공개     화두   연설  
12    규모   보유    법인   최대    지난      중국   국내     미국   사업  
13    조성   이전    계획   구성   부동산      선임   생활    관계자   전국  
14    공급  관계자   메모리  글로벌    부품      지난   기술  디스플레이   전망  
15  석유화학  자동차   자원부   달러    주력      미국   관세    반도체   기간  
16    연구   공정    효율   전력    제작      성능   구조     방식   설명  
17    추구   사진    종이   체제    발행    조직개편   통합     참석   인수  
18    복지   반복   반도체   조사    취재      수사   장소     순간   공장  
19    건설   통신    장비  자동차   텍사스     스위스   산업     개월   경기

In [42]:
result2

0      1    2     3    4        5    6     7    8    9     10      11  \
0     지수    서비스   우려    계약   산업     프로그램  일자리    수출   전망   문제     대체      현지   
1     업종  사물인터넷   노트    체결   기술       과학   특수    정부   실적   때문     단일      퀄컴   
2     거래     지능  가능성    장비   위해       표준   정기    업종   투자   대해     광학      미국   
3     오른     통신  불확실    공급   기업       신뢰   개혁    조선   증가   지금     광장      행사   
4     상승    스마트   상황    제조   분야       기여  필요성    경제   예상  대통령   저장장치      발굴   
5     하락    시스템   정책    규모  반도체       합동  최대한  구조조정  반도체   이유  전기자동차      협회   
6     강세     제공   금리    재료   지원       근거   행위   자동차   대비   대한  하드디스크      구글   
7    포인트     기기   부담   반도체   미래     과학기술   권리    규제   개선   당시     지휘     소비자   
8     마감    플랫폼   경기    매출   통해       규명   제재    소비   이익   과정     주역      나선   
9     증시    자동차   주의    변경   사업  미래창조과학부   시사    국산   분석   지난    수상자      시대   
10   코스피     방침   기업    기간   계획       후속   포럼    정책   영업   생각     결실   최고경영자   
11   코스닥     차량   부정    사항   추진       발굴  정치권    의존   증권   현실     복원      세계   
12    종목     정보   기조    답변   협력       수집   가스    재정   상승   가장    자외선      개국   
13  시가총액   빅데이터   침체    대비   개발       계산  돌파구   선진국   지속   의미   인사이트      관심   
14    유가    데이터   요인    전방   정부       제정   거치    항공   기록   상황     재배      참가   
15    매수     전문   미국    공정   성과     항공우주   처벌    불황   유지   처음     내일    전자기기   
16    기관     기능   작용    수주   혁신       포괄   차관  우리나라   기준   시대     본질  라스베이거스   
17    기록    인터넷  리스크    테크   구축       구단   장면    해양   가격   요구     고수      공개   
18   상승세   네트워크   정치  국제무역   적극       명목   통제    수입   라며   가지     상존      화두   
19    전날     센서   위축    중국   전략      유연성  원동력    중국   평균   지적     주석      연설   

     12   13     14    15   16     17   18    19  
0   반도체   지역     시장    수출   사용     사장   건강   제조업  
1    기업   산업     제품    감소   개발     총괄   사고    공식  
2    투자   시설     업계    수입   기술     경영   피해    동향  
3    회사   건설     생산    철강   기존     합병   이해    공업  
4    결정   예정    반도체    증가   적용    텔레콤  노동자    소비  
5    인수   공장   스마트폰    무역  반도체     회장   보건    통계  
6    설립   규모     중국    통상   활용    시너지   발생    설비  
7   외국인  반도체     최대    중국   장치    리더십   안전    생산  
8    관련  경기도     사업    선박   이용     부문   사망    차질  
9    화학   위치     세계    별로  차세대  최고경영자   거부    파업  
10   자금   여러     경쟁    산업   최초     조직   인용  서비스업  
11   규모   조성     공급  석유화학   연구     추구   복지    건설  
12   보유   이전    관계자   자동차   공정     사진   반복    통신  
13   법인   계획    메모리   자원부   효율     종이  반도체    장비  
14   최대   구성    글로벌    달러   전력     체제   조사   자동차  
15   지난  부동산     부품    주력   제작     발행   취재   텍사스  
16   중국   선임     지난    미국   성능   조직개편   수사   스위스  
17   국내   생활     기술    관세   구조     통합   장소    산업  
18   미국  관계자  디스플레이   반도체   방식     참석   순간    개월  
19   사업   전국     전망    기간   설명     인수   공장    경기

In [43]:
# 엑셀 저장

#result2.to_excel('D:\\toy\\data\\topic_keyword.xlsx')